In [0]:
storage_account = "stgpricing"  # Your storage account name
storage_key = "LyPWzvZumroSkuZcBQKqDU8mXYz0nHSjqewWC2qnVRr+v2/6jHpEAmSI8yNXVbCMV+5uPUcj5cGj+AStYw3TXg=="  # One of the keys from Access Keys

configs = {
    f"fs.azure.account.key.{storage_account}.blob.core.windows.net": storage_key
}

# Unmount any previous failed mounts
for mount in ["/mnt/raw-data", "/mnt/cleand-data"]:
    mounts = [m.mountPoint for m in dbutils.fs.mounts()]
    if mount in mounts:
        dbutils.fs.unmount(mount)

# Mount the raw-data container
dbutils.fs.mount(
    source=f"wasbs://raw-data@{storage_account}.blob.core.windows.net/",
    mount_point="/mnt/raw-data",
    extra_configs=configs
)

# Mount the clean-data container
dbutils.fs.mount(
    source=f"wasbs://cleand-data@{storage_account}.blob.core.windows.net/",
    mount_point="/mnt/cleand-data",
    extra_configs=configs
)

# Verify
raw_data_files = dbutils.fs.ls("/mnt/raw-data")
clean_data_files = dbutils.fs.ls("/mnt/cleand-data")

if raw_data_files:
    display(raw_data_files)
else:
    print("No files found in /mnt/raw-data")

if clean_data_files:
    display(clean_data_files)
else:
    print("No files found in /mnt/cleand-data")

/mnt/raw-data has been unmounted.
/mnt/cleand-data has been unmounted.


path name size modificationTime dbfs:/mnt/raw-data/MA-BMC.csv MA-BMC.csv 1200214864 1746415617000 dbfs:/mnt/raw-data/MA-BWFH.csv MA-BWFH.csv 905884576 1746415599000 dbfs:/mnt/raw-data/MA-MGH.csv MA-MGH.csv 1931299585 1746415651000

path name size modificationTime dbfs:/mnt/cleand-data/MA-BMC-Cleaned/ MA-BMC-Cleaned/ 0 0 dbfs:/mnt/cleand-data/MA-BWFH-Cleaned/ MA-BWFH-Cleaned/ 0 0 dbfs:/mnt/cleand-data/MA-MGH-Cleaned/ MA-MGH-Cleaned/ 0 0

In [0]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

In [0]:
# 1) Imports
from pyspark.sql.functions import col, when, sum as _sum

In [0]:
from pyspark.sql.functions import col, count, lit

# already set spark.conf for storage_account & key above

# ------- For MA-MGH.csv -------
file_2 = "MA-MGH.csv"
clean_folder_2 = file_2.replace(".csv", "-Cleaned")
print(f"\n--- Processing {file_2} → {clean_folder_2} ---")

lines_2 = spark.sparkContext.textFile(f"/mnt/raw-data/{file_2}")
data_rdd_2 = (
    lines_2.zipWithIndex()
           .filter(lambda x: x[1] >= 2)
           .map(lambda x: x[0])
)
df_2 = (
    spark.read
         .option("header", "true")
         .option("encoding", "ISO-8859-1")
         .csv(data_rdd_2)
)
drop_cols = ["additional_generic_notes","setting",
             "drug_unit_of_measurement","drug_type_of_measurement","modifiers"]
df_2 = df_2.drop(*drop_cols)
df_2 = (df_2.filter(col("code|2|type") == "CPT")
             .drop("code|1", "code|1|type", "code|3", "code|3|type", "code|4", "code|4|type"))

dup_counts_2 = df_2.groupBy(df_2.columns).agg(count("*").alias("cnt"))
df_2 = dup_counts_2.filter(col("cnt") == 1).drop("cnt")

null_subset = [
    "standard_charge|gross",
    "standard_charge|discounted_cash",
    "standard_charge|negotiated_dollar",
    "estimated_amount",
    "standard_charge|min",
    "standard_charge|max"
]
df_2 = df_2.na.drop(subset=null_subset)

df_2 = (
    df_2.withColumn("standard_charge|gross", col("standard_charge|gross").cast("double"))
        .withColumn("standard_charge|discounted_cash", col("standard_charge|discounted_cash").cast("double"))
        .withColumn("standard_charge|negotiated_dollar", col("standard_charge|negotiated_dollar").cast("double"))
        .withColumn("standard_charge|negotiated_percentage", col("standard_charge|negotiated_percentage").cast("double"))
        .withColumn("estimated_amount", col("estimated_amount").cast("double"))
        .withColumn("standard_charge|min", col("standard_charge|min").cast("double"))
        .withColumn("standard_charge|max", col("standard_charge|max").cast("double"))
        .withColumn("description", col("description").cast("string"))
        .withColumn("code|2", col("code|2").cast("string"))
        .withColumn("code|2|type", col("code|2|type").cast("string"))
        .withColumn("payer_name", col("payer_name").cast("string"))
        .withColumn("plan_name", col("plan_name").cast("string"))
        .withColumn("standard_charge|negotiated_algorithm", col("standard_charge|negotiated_algorithm").cast("string"))
        .withColumn("standard_charge|methodology", col("standard_charge|methodology").cast("string"))
)
df_2 = df_2 \
    .withColumn("hospital_id", lit("MA-MGH")) \
    .withColumn("hospital_name", lit("Massachusetts General Hospital (MGH)"))

target_2 = f"abfss://cleaned-data@{storage_account}.dfs.core.windows.net/{clean_folder_2}"

df_2.coalesce(1) \
    .write \
    .option("header", True) \
    .mode("overwrite") \
    .csv(target_2)

print(f"Wrote cleaned data as CSV to {target_2}")



--- Processing MA-MGH.csv → MA-MGH-Cleaned ---


---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-5887075155441666>, line 67
     57 df_2 = df_2 \
     58     .withColumn("hospital_id", lit("MA-MGH")) \
     59     .withColumn("hospital_name", lit("Massachusetts General Hospital (MGH)"))
     61 target_2 = f"abfss://cleaned-data@{storage_account}.dfs.core.windows.net/{clean_folder_2}"
     63 df_2.coalesce(1) \
     64     .write \
     65     .option("header", True) \
     66     .mode("overwrite") \
---> 67     .csv(target_2)
     69 print(f"Wrote cleaned data as CSV to {target_2}")

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
    

In [0]:
from pyspark.sql.functions import col, count, lit

storage_account = "stgpricing"
storage_account_key = "LyPWzvZumroSkuZcBQKqDU8mXYz0nHSjqewWC2qnVRr+v2/6jHpEAmSI8yNXVbCMV+5uPUcj5cGj+AStYw3TXg=="

spark.conf.set(f"fs.azure.account.key.{storage_account}.dfs.core.windows.net", storage_account_key)

# ------- For MA-BWFH.csv -------
file_1 = "MA-BWFH.csv"
clean_folder_1 = file_1.replace(".csv", "-Cleaned")
print(f"\n--- Processing {file_1} → {clean_folder_1} ---")

lines_1 = spark.sparkContext.textFile(f"/mnt/raw-data/{file_1}")
data_rdd_1 = (
    lines_1.zipWithIndex()
           .filter(lambda x: x[1] >= 2)
           .map(lambda x: x[0])
)
df_1 = (
    spark.read
         .option("header", "true")
         .option("encoding", "ISO-8859-1")
         .csv(data_rdd_1)
)
drop_cols    = ["additional_generic_notes","setting",
                "drug_unit_of_measurement","drug_type_of_measurement","modifiers"]
df_1 = df_1.drop(*drop_cols)
df_1 = (df_1.filter(col("code|2|type") == "CPT")
             .drop("code|1", "code|1|type", "code|3", "code|3|type", "code|4", "code|4|type"))

dup_counts_1 = df_1.groupBy(df_1.columns).agg(count("*").alias("cnt"))
df_1 = dup_counts_1.filter(col("cnt") == 1).drop("cnt")
null_subset = [
    "standard_charge|gross",
    "standard_charge|discounted_cash",
    "standard_charge|negotiated_dollar",
    "estimated_amount",
    "standard_charge|min",
    "standard_charge|max"
]
df_1 = df_1.na.drop(subset=null_subset)

df_1 = (
    df_1.withColumn("standard_charge|gross", col("standard_charge|gross").cast("double"))
        .withColumn("standard_charge|discounted_cash", col("standard_charge|discounted_cash").cast("double"))
        .withColumn("standard_charge|negotiated_dollar", col("standard_charge|negotiated_dollar").cast("double"))
        .withColumn("standard_charge|negotiated_percentage", col("standard_charge|negotiated_percentage").cast("double"))
        .withColumn("estimated_amount", col("estimated_amount").cast("double"))
        .withColumn("standard_charge|min", col("standard_charge|min").cast("double"))
        .withColumn("standard_charge|max", col("standard_charge|max").cast("double"))
        .withColumn("description", col("description").cast("string"))
        .withColumn("code|2", col("code|2").cast("string"))
        .withColumn("code|2|type", col("code|2|type").cast("string"))
        .withColumn("payer_name", col("payer_name").cast("string"))
        .withColumn("plan_name", col("plan_name").cast("string"))
        .withColumn("standard_charge|negotiated_algorithm", col("standard_charge|negotiated_algorithm").cast("string"))
        .withColumn("standard_charge|methodology", col("standard_charge|methodology").cast("string"))
)
df_1 = df_1 \
    .withColumn("hospital_id", lit("MA-2048")) \
    .withColumn("hospital_name", lit("Brigham and Women's Faulkner Hospital (BWFH)"))

target_1 = f"abfss://cleand-data@{storage_account}.dfs.core.windows.net/{clean_folder_1}"


df_1.coalesce(1) \
    .write \
    .option("header", True) \
    .mode("overwrite") \
    .csv(target_1)

print(f"Wrote cleaned data as CSV to {target_1}")


--- Processing MA-BWFH.csv → MA-BWFH-Cleaned ---
Wrote cleaned data as CSV to abfss://cleand-data@stgpricing.dfs.core.windows.net/MA-BWFH-Cleaned


In [0]:
display(df_1)

description code|2 code|2|type standard_charge|gross standard_charge|discounted_cash payer_name plan_name standard_charge|negotiated_dollar standard_charge|negotiated_percentage standard_charge|negotiated_algorithm estimated_amount standard_charge|min standard_charge|max standard_charge|methodology hospital_id hospital_name Nonphysician Telephone Assessment 11-20 Min (Pt) 98967 CPT 107.0 80.25 COMMONWEALTH CARE ALLIANCE [1007] COMMONWEALTH CARE ALLIANCE ONE CARE MEDICARE REPLACEMENT [100702] 22.67 null null 22.67 22.67 72.1 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Ephys Eval Pacg Cvdfb Prgrmg/Reprgrmg Parameters 93642 CPT 13651.0 10238.25 HUMANA [1012] HUMANA PPO MEDICARE REPLACEMENT [101204] 95.73 null null 95.73 95.73 2215.48 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Emg Cranial Nerve Unilat 95867 CPT 446.0 334.5 MEDICARE [2001] MEDICARE RAILROAD [200105] 77.11 null null 77.11 77.11 519.72 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Morpho Analysis Insitu Hybrid Man 88368 CPT 854.0 640.5 GENERIC MEDICARE REPLACEMENT [1010] WELLSENSE NH MEDICARE REPLACEMENT [101004] 126.01 null null 126.01 126.01 184.01 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Egd Endo Mucosal Resection 43254 CPT 2191.0 1643.25 HARVARD PILGRIM [120001] HARVARD PILGRIM STRIDE MEDICARE REPLACEMENT [12000109] 281.23 null null 281.23 281.23 1334.83 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Colposcopy W/Bx Vagina/Cervix 57421 CPT 1206.0 904.5 MEDICARE [2001] MEDICARE B [200102] 128.13 null null 128.13 128.13 665.87 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Fitting/Insertion Pessary 57160 CPT 414.0 310.5 MGB HEALTH PLAN [150001] MGBHP GIC COMPLETE HMO [15000118] 152.21 null null 152.21 47.79 152.21 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Exc Lesion Vestib Mouth W/O Rpr 40810 CPT 3981.0 2985.75 CIGNA [1006] CIGNA MVP MEDICARE REPLACEMENT [100610] 136.43 null null 136.43 136.43 2173.69 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Egd Flex Dx W/Brushing/Washing 43235 CPT 2050.0 1537.5 HUMANA [1012] HUMANA PPO MEDICARE REPLACEMENT [101204] 129.09 null null 129.09 129.09 2088.0 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Rast Allergen Ige Qn Sq Ea 86003 CPT 60.0 45.0 GENERIC MEDICARE REPLACEMENT [1010] GENERIC MEDICARE REPLACEMENT [101001] 5.22 null null 5.22 5.12 20.71 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Facet Denervation� <80 Degrees Celcius: Cervical or Thoracic; Single 64999 CPT 968.0 726.0 MGB HEALTH PLAN [150001] MGBHP HMO [15000102] 1968.0 null null 968.0 1968.0 2088.0 per diem MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Nfct Ds Bct Fng Parasite Dna Vir Detcj >1000 Org 0152U CPT 4223.0 3167.25 CHAMPVA [160001] CHAMPVA [16000101] 2126.2 null null 2126.2 2083.68 2189.99 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Sbsq Hospital IP/Obs Care Sf/Low Mdm 25 Minutes 99231 CPT 210.0 157.5 FALLON HEALTH [1008] FALLON MEDICARE REPLACEMENT [100803] 51.65 null null 51.65 50.62 53.2 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Prq Skel Fixj Dstl Phlngl Fx Fngr/Thmb Ea 26756 CPT 6934.0 5200.5 MGB HEALTH PLAN [150001] MGBHP GIC COMPLETE HMO [15000118] 1968.0 null null 1968.0 1968.0 2088.0 per diem MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Repl Cath Cv Tnl W/O Port 36581 CPT 4612.0 3459.0 MEDICARE ALTERNATE [2002] MEDICARE RAILROAD PROF [200202] 190.31 null null 190.31 190.31 2088.0 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) CT Head W&W/O Contrast 70470 CPT 2313.0 1734.75 BLUE CROSS BLUE SHIELD [110001] BLUE CROSS OUT OF STATE PPO MEDICARE REPLACEMENT [11000111] 138.94 null null 138.94 138.94 1244.13 fee schedule MA-2048 Brigham and Women's Faulkner Hospital (BWFH) Perq Breast Loc Device Placemt 1st Strtctc Guid 19283 CPT 513.0 384.75 MGB HEALTH PLAN [15000

In [0]:
from pyspark.sql.functions import col, count, lit

# already set spark.conf for storage_account & key above

# ------- For MA-MGH.csv -------
file_2 = "MA-MGH.csv"
clean_folder_2 = file_2.replace(".csv", "-Cleaned")
print(f"\n--- Processing {file_2} → {clean_folder_2} ---")

lines_2 = spark.sparkContext.textFile(f"/mnt/raw-data/{file_2}")
data_rdd_2 = (
    lines_2.zipWithIndex()
           .filter(lambda x: x[1] >= 2)
           .map(lambda x: x[0])
)
df_2 = (
    spark.read
         .option("header", "true")
         .option("encoding", "ISO-8859-1")
         .csv(data_rdd_2)
)
drop_cols = ["additional_generic_notes","setting",
             "drug_unit_of_measurement","drug_type_of_measurement","modifiers"]
df_2 = df_2.drop(*drop_cols)
df_2 = (df_2.filter(col("code|2|type") == "CPT")
             .drop("code|1", "code|1|type", "code|3", "code|3|type", "code|4", "code|4|type"))

dup_counts_2 = df_2.groupBy(df_2.columns).agg(count("*").alias("cnt"))
df_2 = dup_counts_2.filter(col("cnt") == 1).drop("cnt")

null_subset = [
    "standard_charge|gross",
    "standard_charge|discounted_cash",
    "standard_charge|negotiated_dollar",
    "estimated_amount",
    "standard_charge|min",
    "standard_charge|max"
]
df_2 = df_2.na.drop(subset=null_subset)

df_2 = (
    df_2.withColumn("standard_charge|gross", col("standard_charge|gross").cast("double"))
        .withColumn("standard_charge|discounted_cash", col("standard_charge|discounted_cash").cast("double"))
        .withColumn("standard_charge|negotiated_dollar", col("standard_charge|negotiated_dollar").cast("double"))
        .withColumn("standard_charge|negotiated_percentage", col("standard_charge|negotiated_percentage").cast("double"))
        .withColumn("estimated_amount", col("estimated_amount").cast("double"))
        .withColumn("standard_charge|min", col("standard_charge|min").cast("double"))
        .withColumn("standard_charge|max", col("standard_charge|max").cast("double"))
        .withColumn("description", col("description").cast("string"))
        .withColumn("code|2", col("code|2").cast("string"))
        .withColumn("code|2|type", col("code|2|type").cast("string"))
        .withColumn("payer_name", col("payer_name").cast("string"))
        .withColumn("plan_name", col("plan_name").cast("string"))
        .withColumn("standard_charge|negotiated_algorithm", col("standard_charge|negotiated_algorithm").cast("string"))
        .withColumn("standard_charge|methodology", col("standard_charge|methodology").cast("string"))
)
df_2 = df_2 \
    .withColumn("hospital_id", lit("MA-MGH")) \
    .withColumn("hospital_name", lit("Massachusetts General Hospital (MGH)"))

target_2 = f"abfss://cleand-data@{storage_account}.dfs.core.windows.net/{clean_folder_2}"

df_2.coalesce(1) \
    .write \
    .option("header", True) \
    .mode("overwrite") \
    .csv(target_2)

print(f"Wrote cleaned data as CSV to {target_2}")



--- Processing MA-MGH.csv → MA-MGH-Cleaned ---
Wrote cleaned data as CSV to abfss://cleand-data@stgpricing.dfs.core.windows.net/MA-MGH-Cleaned


In [0]:
from pyspark.sql.functions import col, count, lit

# ------- For MA-BMC.csv -------
file_3 = "MA-BMC.csv"
clean_folder_3 = file_3.replace(".csv", "-Cleaned")
print(f"\n--- Processing {file_3} → {clean_folder_3} ---")

lines_3 = spark.sparkContext.textFile(f"/mnt/raw-data/{file_3}")
data_rdd_3 = (
    lines_3.zipWithIndex()
           .filter(lambda x: x[1] >= 2)
           .map(lambda x: x[0])
)
df_3 = (
    spark.read
         .option("header", "true")
         .option("encoding", "ISO-8859-1")
         .csv(data_rdd_3)
)
drop_cols = ["additional_generic_notes","setting",
             "drug_unit_of_measurement","drug_type_of_measurement","modifiers"]
df_3 = df_3.drop(*drop_cols)
df_3 = (df_3.filter(col("code|2|type") == "CPT")
             .drop("code|1", "code|1|type", "code|3", "code|3|type", "code|4", "code|4|type"))

dup_counts_3 = df_3.groupBy(df_3.columns).agg(count("*").alias("cnt"))
df_3 = dup_counts_3.filter(col("cnt") == 1).drop("cnt")

null_subset = [
    "standard_charge|gross",
    "standard_charge|discounted_cash",
    "standard_charge|negotiated_dollar",
    "estimated_amount",
    "standard_charge|min",
    "standard_charge|max"
]
df_3 = df_3.na.drop(subset=null_subset)

df_3 = (
    df_3.withColumn("standard_charge|gross", col("standard_charge|gross").cast("double"))
        .withColumn("standard_charge|discounted_cash", col("standard_charge|discounted_cash").cast("double"))
        .withColumn("standard_charge|negotiated_dollar", col("standard_charge|negotiated_dollar").cast("double"))
        .withColumn("standard_charge|negotiated_percentage", col("standard_charge|negotiated_percentage").cast("double"))
        .withColumn("estimated_amount", col("estimated_amount").cast("double"))
        .withColumn("standard_charge|min", col("standard_charge|min").cast("double"))
        .withColumn("standard_charge|max", col("standard_charge|max").cast("double"))
        .withColumn("description", col("description").cast("string"))
        .withColumn("code|2", col("code|2").cast("string"))
        .withColumn("code|2|type", col("code|2|type").cast("string"))
        .withColumn("payer_name", col("payer_name").cast("string"))
        .withColumn("plan_name", col("plan_name").cast("string"))
        .withColumn("standard_charge|negotiated_algorithm", col("standard_charge|negotiated_algorithm").cast("string"))
        .withColumn("standard_charge|methodology", col("standard_charge|methodology").cast("string"))
)
df_3 = df_3 \
    .withColumn("hospital_id", lit("MA-BMC")) \
    .withColumn("hospital_name", lit("Boston Medical Center (BMC)"))

target_3 = f"abfss://cleand-data@{storage_account}.dfs.core.windows.net/{clean_folder_3}"

df_3.coalesce(1) \
    .write \
    .option("header", True) \
    .mode("overwrite") \
    .csv(target_3)

print(f"Wrote cleaned data as CSV to {target_3}")



--- Processing MA-BMC.csv → MA-BMC-Cleaned ---
Wrote cleaned data as CSV to abfss://cleand-data@stgpricing.dfs.core.windows.net/MA-BMC-Cleaned
